# 🧠 Fraud Detection Pipeline - Part 5: Deep Learning Models

## 📋 Overview
This notebook covers training Deep Learning models:
- Multi-Layer Perceptron (MLP)
- Deep Neural Network with Regularization
- Autoencoder for Anomaly Detection

Including:
- Custom loss functions for imbalanced data
- Learning rate scheduling
- Early stopping
- Model checkpointing

---

## 1️⃣ Setup & Load Data

In [ ]:
!pip install -q tensorflow keras

In [4]:
import os
BASE_PATH = os.path.abspath('.')

In [ ]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

import tensorflow as tf
from tensorflow import keras
from tensorflow.keras import layers, Model, regularizers
from tensorflow.keras.callbacks import EarlyStopping, ModelCheckpoint, ReduceLROnPlateau, TensorBoard
from tensorflow.keras.optimizers import Adam

from sklearn.metrics import (
    classification_report, confusion_matrix, roc_auc_score,
    precision_recall_curve, roc_curve, average_precision_score,
    f1_score, precision_score, recall_score, accuracy_score
)

import pickle
import json
import time
import warnings
import gc
warnings.filterwarnings('ignore')

print(f'TensorFlow version: {tf.__version__}')
print(f'GPU available: {tf.config.list_physical_devices("GPU")}')

COLORS = {
    'primary': '#3498db',
    'secondary': '#2ecc71',
    'danger': '#e74c3c',
    'warning': '#f39c12',
    'info': '#9b59b6'
}

print('\n✅ Libraries imported!')

In [6]:
X_train = np.load(f'{BASE_PATH}/data/splits/X_train.npy')
X_val = np.load(f'{BASE_PATH}/data/splits/X_val.npy')
X_holdout = np.load(f'{BASE_PATH}/data/splits/X_holdout.npy')
y_train = np.load(f'{BASE_PATH}/data/splits/y_train.npy')
y_val = np.load(f'{BASE_PATH}/data/splits/y_val.npy')
y_holdout = np.load(f'{BASE_PATH}/data/splits/y_holdout.npy')

with open(f'{BASE_PATH}/reports/metrics/feature_engineering_info.json', 'r') as f:
    feat_info = json.load(f)

N_FEATURES = X_train.shape[1]

print(f'📊 Train: {X_train.shape}')
print(f'📊 Validation: {X_val.shape}')
print(f'📊 Holdout: {X_holdout.shape}')
print(f'📊 Features: {N_FEATURES}')
print(f'\n🎯 Fraud rate - Train: {y_train.mean()*100:.2f}%, Val: {y_val.mean()*100:.2f}%')

📊 Train: (472432, 91)
📊 Validation: (59054, 91)
📊 Holdout: (59054, 91)
📊 Features: 91

🎯 Fraud rate - Train: 3.50%, Val: 3.50%


In [7]:
n_fraud = y_train.sum()
n_legit = len(y_train) - n_fraud

class_weight = {
    0: len(y_train) / (2 * n_legit),
    1: len(y_train) / (2 * n_fraud)
}

print(f'⚖️ Class weights:')
print(f'  Class 0 (Legit): {class_weight[0]:.4f}')
print(f'  Class 1 (Fraud): {class_weight[1]:.4f}')

⚖️ Class weights:
  Class 0 (Legit): 0.5181
  Class 1 (Fraud): 14.2901


## 2️⃣ Utility Functions

In [8]:
def evaluate_dl_model(model, X, y, model_name, threshold=0.5):
    """
    Comprehensive DL model evaluation
    """
    y_pred_proba = model.predict(X, verbose=0).flatten()
    y_pred = (y_pred_proba >= threshold).astype(int)
    
    metrics = {
        'model': model_name,
        'accuracy': accuracy_score(y, y_pred),
        'precision': precision_score(y, y_pred),
        'recall': recall_score(y, y_pred),
        'f1': f1_score(y, y_pred),
        'roc_auc': roc_auc_score(y, y_pred_proba),
        'pr_auc': average_precision_score(y, y_pred_proba)
    }
    
    return metrics, y_pred, y_pred_proba

In [9]:
def plot_training_history(history, model_name):
    """
    Plot training history with beautiful charts
    """
    fig = make_subplots(
        rows=1, cols=2,
        subplot_titles=('Loss', 'AUC')
    )
    
    epochs = list(range(1, len(history.history['loss']) + 1))
    
    fig.add_trace(
        go.Scatter(x=epochs, y=history.history['loss'], name='Train Loss',
                   line=dict(color=COLORS['primary'])),
        row=1, col=1
    )
    fig.add_trace(
        go.Scatter(x=epochs, y=history.history['val_loss'], name='Val Loss',
                   line=dict(color=COLORS['danger'])),
        row=1, col=1
    )
    
    if 'auc' in history.history:
        fig.add_trace(
            go.Scatter(x=epochs, y=history.history['auc'], name='Train AUC',
                       line=dict(color=COLORS['secondary'])),
            row=1, col=2
        )
        fig.add_trace(
            go.Scatter(x=epochs, y=history.history['val_auc'], name='Val AUC',
                       line=dict(color=COLORS['warning'])),
            row=1, col=2
        )
    
    fig.update_layout(
        title=f'📈 {model_name} Training History',
        title_font_size=18,
        height=400
    )
    
    fig.update_xaxes(title_text='Epoch')
    
    return fig

In [10]:
def plot_model_performance(y_true, y_pred, y_proba, model_name):
    """
    Plot comprehensive model performance
    """
    fig = make_subplots(
        rows=2, cols=2,
        subplot_titles=(
            'Confusion Matrix',
            'ROC Curve',
            'Precision-Recall Curve',
            'Prediction Distribution'
        ),
        specs=[[{'type': 'heatmap'}, {'type': 'scatter'}],
               [{'type': 'scatter'}, {'type': 'histogram'}]]
    )
    
    cm = confusion_matrix(y_true, y_pred)
    cm_normalized = cm.astype('float') / cm.sum(axis=1)[:, np.newaxis]
    
    fig.add_trace(
        go.Heatmap(
            z=cm_normalized,
            x=['Pred Legit', 'Pred Fraud'],
            y=['Actual Legit', 'Actual Fraud'],
            colorscale='Blues',
            text=cm,
            texttemplate='%{text:,}',
            showscale=False
        ),
        row=1, col=1
    )
    
    fpr, tpr, _ = roc_curve(y_true, y_proba)
    roc_auc = roc_auc_score(y_true, y_proba)
    
    fig.add_trace(
        go.Scatter(
            x=fpr, y=tpr,
            mode='lines',
            name=f'ROC (AUC={roc_auc:.4f})',
            line=dict(color=COLORS['primary'], width=2)
        ),
        row=1, col=2
    )
    fig.add_trace(
        go.Scatter(x=[0, 1], y=[0, 1], mode='lines',
                   line=dict(color='gray', dash='dash'), showlegend=False),
        row=1, col=2
    )
    
    precision, recall, _ = precision_recall_curve(y_true, y_proba)
    pr_auc = average_precision_score(y_true, y_proba)
    
    fig.add_trace(
        go.Scatter(
            x=recall, y=precision,
            mode='lines',
            name=f'PR (AUC={pr_auc:.4f})',
            line=dict(color=COLORS['secondary'], width=2)
        ),
        row=2, col=1
    )
    
    fig.add_trace(
        go.Histogram(x=y_proba[y_true == 0], name='Legitimate',
                     marker_color=COLORS['secondary'], opacity=0.7, nbinsx=50),
        row=2, col=2
    )
    fig.add_trace(
        go.Histogram(x=y_proba[y_true == 1], name='Fraud',
                     marker_color=COLORS['danger'], opacity=0.7, nbinsx=50),
        row=2, col=2
    )
    
    fig.update_layout(
        title=f'📊 {model_name} Performance',
        title_font_size=20,
        height=700
    )
    
    return fig

In [11]:
all_results = []
trained_models = {}

## 3️⃣ Model 1: Basic MLP

In [12]:
def create_mlp_model(input_dim, name='MLP'):
    """
    Create a basic Multi-Layer Perceptron
    """
    model = keras.Sequential([
        layers.Input(shape=(input_dim,)),
        layers.Dense(256, activation='relu'),
        layers.BatchNormalization(),
        layers.Dropout(0.3),
        layers.Dense(128, activation='relu'),
        layers.BatchNormalization(),
        layers.Dropout(0.3),
        layers.Dense(64, activation='relu'),
        layers.BatchNormalization(),
        layers.Dropout(0.2),
        layers.Dense(32, activation='relu'),
        layers.Dense(1, activation='sigmoid')
    ], name=name)
    
    return model

In [13]:
mlp_model = create_mlp_model(N_FEATURES, name='Basic_MLP')

mlp_model.compile(
    optimizer=Adam(learning_rate=0.001),
    loss='binary_crossentropy',
    metrics=['accuracy', keras.metrics.AUC(name='auc')]
)

mlp_model.summary()

Model: "Basic_MLP"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ dense (Dense)                   │ (None, 256)            │        23,552 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization             │ (None, 256)            │         1,024 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout (Dropout)               │ (None, 256)            │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_1 (Dense)                 │ (None, 128)            │        32,896 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_1           │ (None, 128)            │           512 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_1 (Dropout)             │ (None, 128)            │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_2 (Dense)                 │ (None, 64)             │         8,256 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_2           │ (None, 64)             │           256 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_2 (Dropout)             │ (None, 64)             │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_3 (Dense)                 │ (None, 32)             │         2,080 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_4 (Dense)                 │ (None, 1)              │            33 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 68,609 (268.00 KB)

 Trainable params: 67,713 (264.50 KB)

 Non-trainable params: 896 (3.50 KB)

In [14]:
callbacks_mlp = [
    EarlyStopping(
        monitor='val_auc',
        patience=10,
        mode='max',
        restore_best_weights=True,
        verbose=1
    ),
    ReduceLROnPlateau(
        monitor='val_loss',
        factor=0.5,
        patience=5,
        min_lr=1e-6,
        verbose=1
    ),
    ModelCheckpoint(
        f'{BASE_PATH}/models/dl/mlp_best.keras',
        monitor='val_auc',
        mode='max',
        save_best_only=True,
        verbose=0
    )
]

In [15]:
print('🔧 Training Basic MLP...')
start_time = time.time()

history_mlp = mlp_model.fit(
    X_train, y_train,
    validation_data=(X_val, y_val),
    epochs=100,
    batch_size=2048,
    class_weight=class_weight,
    callbacks=callbacks_mlp,
    verbose=1
)

train_time = time.time() - start_time
print(f'\n✅ Training complete in {train_time:.2f}s')

🔧 Training Basic MLP...
Epoch 1/100
231/231 ━━━━━━━━━━━━━━━━━━━━ 9s 28ms/step - accuracy: 0.7390 - auc: 0.7970 - loss: 0.5516 - val_accuracy: 0.8289 - val_auc: 0.8392 - val_loss: 0.3981 - learning_rate: 0.0010
Epoch 2/100
231/231 ━━━━━━━━━━━━━━━━━━━━ 14s 58ms/step - accuracy: 0.7543 - auc: 0.8267 - loss: 0.5089 - val_accuracy: 0.8278 - val_auc: 0.8477 - val_loss: 0.4063 - learning_rate: 0.0010
Epoch 3/100
231/231 ━━━━━━━━━━━━━━━━━━━━ 14s 59ms/step - accuracy: 0.7703 - auc: 0.8346 - loss: 0.4983 - val_accuracy: 0.8299 - val_auc: 0.8537 - val_loss: 0.4131 - learning_rate: 0.0010
Epoch 4/100
231/231 ━━━━━━━━━━━━━━━━━━━━ 13s 57ms/step - accuracy: 0.7770 - auc: 0.8410 - loss: 0.4894 - val_accuracy: 0.8228 - val_auc: 0.8576 - val_loss: 0.4126 - learning_rate: 0.0010
Epoch 5/100
231/231 ━━━━━━━━━━━━━━━━━━━━ 14s 62ms/step - accuracy: 0.7802 - auc: 0.8443 - loss: 0.4847 - val_accuracy: 0.8351 - val_auc: 0.8587 - val_loss: 0.3870 - learning_rate: 0.0010
Epoch 6/100
231/231 ━━━━━━━━━━━━━━━━━━━━ 6

In [16]:
fig = plot_training_history(history_mlp, 'Basic MLP')
fig.show()
fig.write_html(f'{BASE_PATH}/reports/figures/22_mlp_training.html')

In [17]:
mlp_metrics, mlp_pred, mlp_proba = evaluate_dl_model(mlp_model, X_val, y_val, 'Basic MLP')
mlp_metrics['train_time'] = train_time
all_results.append(mlp_metrics)
trained_models['mlp'] = mlp_model

print('📊 Validation Results:')
for k, v in mlp_metrics.items():
    if k != 'model':
        print(f'  {k}: {v:.4f}' if isinstance(v, float) else f'  {k}: {v}')

📊 Validation Results:
  accuracy: 0.8457
  precision: 0.1530
  recall: 0.7518
  f1: 0.2543
  roc_auc: 0.8831
  pr_auc: 0.4690
  train_time: 796.8049


In [18]:
fig = plot_model_performance(y_val, mlp_pred, mlp_proba, 'Basic MLP')
fig.show()
fig.write_html(f'{BASE_PATH}/reports/figures/23_mlp_performance.html')

## 4️⃣ Model 2: Deep Neural Network with Advanced Regularization

In [19]:
def create_deep_nn(input_dim, name='Deep_NN'):
    """
    Create a deeper neural network with advanced regularization
    """
    inputs = layers.Input(shape=(input_dim,))
    
    x = layers.Dense(512, kernel_regularizer=regularizers.l2(0.001))(inputs)
    x = layers.BatchNormalization()(x)
    x = layers.Activation('relu')(x)
    x = layers.Dropout(0.4)(x)
    
    x = layers.Dense(256, kernel_regularizer=regularizers.l2(0.001))(x)
    x = layers.BatchNormalization()(x)
    x = layers.Activation('relu')(x)
    x = layers.Dropout(0.4)(x)
    
    x1 = layers.Dense(128, kernel_regularizer=regularizers.l2(0.001))(x)
    x1 = layers.BatchNormalization()(x1)
    x1 = layers.Activation('relu')(x1)
    x1 = layers.Dropout(0.3)(x1)
    
    x = layers.Dense(64, kernel_regularizer=regularizers.l2(0.001))(x1)
    x = layers.BatchNormalization()(x)
    x = layers.Activation('relu')(x)
    x = layers.Dropout(0.2)(x)
    
    x = layers.Dense(32, kernel_regularizer=regularizers.l2(0.001))(x)
    x = layers.BatchNormalization()(x)
    x = layers.Activation('relu')(x)
    
    outputs = layers.Dense(1, activation='sigmoid')(x)
    
    model = Model(inputs=inputs, outputs=outputs, name=name)
    return model

In [21]:
def focal_loss(gamma=2.0, alpha=0.25):
    """
    Focal loss for handling class imbalance
    """
    def focal_loss_fn(y_true, y_pred):
        y_true = tf.cast(y_true, tf.float32)
        y_pred = tf.clip_by_value(y_pred, 1e-7, 1 - 1e-7)
        
        cross_entropy = -y_true * tf.math.log(y_pred) - (1 - y_true) * tf.math.log(1 - y_pred)
        
        p_t = y_true * y_pred + (1 - y_true) * (1 - y_pred)
        alpha_t = y_true * alpha + (1 - y_true) * (1 - alpha)
        focal_weight = alpha_t * tf.pow(1 - p_t, gamma)
        
        return tf.reduce_mean(focal_weight * cross_entropy)
    
    return focal_loss_fn

In [22]:
deep_nn = create_deep_nn(N_FEATURES, name='Deep_NN')

deep_nn.compile(
    optimizer=Adam(learning_rate=0.0005),
    loss=focal_loss(gamma=2.0, alpha=0.25),
    metrics=['accuracy', keras.metrics.AUC(name='auc')]
)

deep_nn.summary()

Model: "Deep_NN"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ input_layer_1 (InputLayer)      │ (None, 91)             │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_5 (Dense)                 │ (None, 512)            │        47,104 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_3           │ (None, 512)            │         2,048 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ activation (Activation)         │ (None, 512)            │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_3 (Dropout)             │ (None, 512)            │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_6 (Dense)                 │ (None, 256)            │       131,328 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_4           │ (None, 256)            │         1,024 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ activation_1 (Activation)       │ (None, 256)            │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_4 (Dropout)             │ (None, 256)            │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_7 (Dense)                 │ (None, 128)            │        32,896 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_5           │ (None, 128)            │           512 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ activation_2 (Activation)       │ (None, 128)            │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_5 (Dropout)             │ (None, 128)            │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_8 (Dense)                 │ (None, 64)             │         8,256 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_6           │ (None, 64)             │           256 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ activation_3 (Activation)       │ (None, 64)             │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_6 (Dropout)             │ (None, 64)             │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_9 (Dense)                 │ (None, 32)             │         2,080 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_7           │ (None, 32)             │           128 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ activation_4 (Activation)       │ (None, 32)             │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_10 (Dense)                │ (None, 1)              │            33 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 225,665 (881.50 KB)

 Trainable params: 223,681 (873.75 KB)

 Non-trainable params: 1,984 (7.75 KB)

In [23]:
callbacks_dnn = [
    EarlyStopping(
        monitor='val_auc',
        patience=15,
        mode='max',
        restore_best_weights=True,
        verbose=1
    ),
    ReduceLROnPlateau(
        monitor='val_loss',
        factor=0.5,
        patience=5,
        min_lr=1e-7,
        verbose=1
    ),
    ModelCheckpoint(
        f'{BASE_PATH}/models/dl/deep_nn_best.keras',
        monitor='val_auc',
        mode='max',
        save_best_only=True,
        verbose=0
    )
]

In [24]:
print('🔧 Training Deep Neural Network with Focal Loss...')
start_time = time.time()

history_dnn = deep_nn.fit(
    X_train, y_train,
    validation_data=(X_val, y_val),
    epochs=100,
    batch_size=2048,
    callbacks=callbacks_dnn,
    verbose=1
)

train_time = time.time() - start_time
print(f'\n✅ Training complete in {train_time:.2f}s')

🔧 Training Deep Neural Network with Focal Loss...
Epoch 1/100
231/231 ━━━━━━━━━━━━━━━━━━━━ 24s 92ms/step - accuracy: 0.9588 - auc: 0.5906 - loss: 0.4027 - val_accuracy: 0.9650 - val_auc: 0.7753 - val_loss: 0.1500 - learning_rate: 5.0000e-04
Epoch 2/100
231/231 ━━━━━━━━━━━━━━━━━━━━ 22s 93ms/step - accuracy: 0.9653 - auc: 0.7479 - loss: 0.0768 - val_accuracy: 0.9650 - val_auc: 0.7796 - val_loss: 0.0391 - learning_rate: 5.0000e-04
Epoch 3/100
231/231 ━━━━━━━━━━━━━━━━━━━━ 21s 92ms/step - accuracy: 0.9657 - auc: 0.7840 - loss: 0.0261 - val_accuracy: 0.9650 - val_auc: 0.7957 - val_loss: 0.0195 - learning_rate: 5.0000e-04
Epoch 4/100
231/231 ━━━━━━━━━━━━━━━━━━━━ 21s 92ms/step - accuracy: 0.9659 - auc: 0.7952 - loss: 0.0165 - val_accuracy: 0.9650 - val_auc: 0.8107 - val_loss: 0.0150 - learning_rate: 5.0000e-04
Epoch 5/100
231/231 ━━━━━━━━━━━━━━━━━━━━ 21s 89ms/step - accuracy: 0.9658 - auc: 0.7961 - loss: 0.0143 - val_accuracy: 0.9650 - val_auc: 0.8232 - val_loss: 0.0137 - learning_rate: 5.0000

In [25]:
fig = plot_training_history(history_dnn, 'Deep NN (Focal Loss)')
fig.show()
fig.write_html(f'{BASE_PATH}/reports/figures/24_dnn_training.html')

In [26]:
dnn_metrics, dnn_pred, dnn_proba = evaluate_dl_model(deep_nn, X_val, y_val, 'Deep NN (Focal Loss)')
dnn_metrics['train_time'] = train_time
all_results.append(dnn_metrics)
trained_models['deep_nn'] = deep_nn

print('📊 Validation Results:')
for k, v in dnn_metrics.items():
    if k != 'model':
        print(f'  {k}: {v:.4f}' if isinstance(v, float) else f'  {k}: {v}')

📊 Validation Results:
  accuracy: 0.9708
  precision: 0.9012
  recall: 0.1853
  f1: 0.3074
  roc_auc: 0.8686
  pr_auc: 0.4596
  train_time: 2289.8420


In [27]:
fig = plot_model_performance(y_val, dnn_pred, dnn_proba, 'Deep NN (Focal Loss)')
fig.show()
fig.write_html(f'{BASE_PATH}/reports/figures/25_dnn_performance.html')

## 5️⃣ Model 3: Autoencoder for Anomaly Detection

In [28]:
def create_autoencoder(input_dim, encoding_dim=32):
    """
    Create an autoencoder for anomaly detection
    Train only on legitimate transactions, then use reconstruction error
    """
    inputs = layers.Input(shape=(input_dim,))
    x = layers.Dense(256, activation='relu')(inputs)
    x = layers.BatchNormalization()(x)
    x = layers.Dense(128, activation='relu')(x)
    x = layers.BatchNormalization()(x)
    x = layers.Dense(64, activation='relu')(x)
    encoded = layers.Dense(encoding_dim, activation='relu', name='encoding')(x)
    
    x = layers.Dense(64, activation='relu')(encoded)
    x = layers.BatchNormalization()(x)
    x = layers.Dense(128, activation='relu')(x)
    x = layers.BatchNormalization()(x)
    x = layers.Dense(256, activation='relu')(x)
    decoded = layers.Dense(input_dim, activation='linear')(x)
    
    autoencoder = Model(inputs, decoded, name='Autoencoder')
    encoder = Model(inputs, encoded, name='Encoder')
    
    return autoencoder, encoder

In [29]:
X_train_legit = X_train[y_train == 0]
X_val_legit = X_val[y_val == 0]

print(f'📊 Training data (legit only): {X_train_legit.shape}')
print(f'📊 Validation data (legit only): {X_val_legit.shape}')

📊 Training data (legit only): (455902, 91)
📊 Validation data (legit only): (56987, 91)


In [30]:
autoencoder, encoder = create_autoencoder(N_FEATURES, encoding_dim=32)

autoencoder.compile(
    optimizer=Adam(learning_rate=0.001),
    loss='mse'
)

autoencoder.summary()

Model: "Autoencoder"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ input_layer_2 (InputLayer)      │ (None, 91)             │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_11 (Dense)                │ (None, 256)            │        23,552 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_8           │ (None, 256)            │         1,024 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_12 (Dense)                │ (None, 128)            │        32,896 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_9           │ (None, 128)            │           512 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_13 (Dense)                │ (None, 64)             │         8,256 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ encoding (Dense)                │ (None, 32)             │         2,080 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_14 (Dense)                │ (None, 64)             │         2,112 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_10          │ (None, 64)             │           256 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_15 (Dense)                │ (None, 128)            │         8,320 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_11          │ (None, 128)            │           512 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_16 (Dense)                │ (None, 256)            │        33,024 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_17 (Dense)                │ (None, 91)             │        23,387 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 135,931 (530.98 KB)

 Trainable params: 134,779 (526.48 KB)

 Non-trainable params: 1,152 (4.50 KB)

In [31]:
callbacks_ae = [
    EarlyStopping(
        monitor='val_loss',
        patience=10,
        restore_best_weights=True,
        verbose=1
    ),
    ModelCheckpoint(
        f'{BASE_PATH}/models/dl/autoencoder_best.keras',
        monitor='val_loss',
        save_best_only=True,
        verbose=0
    )
]

In [32]:
print('🔧 Training Autoencoder on legitimate transactions...')
start_time = time.time()

history_ae = autoencoder.fit(
    X_train_legit, X_train_legit,
    validation_data=(X_val_legit, X_val_legit),
    epochs=50,
    batch_size=2048,
    callbacks=callbacks_ae,
    verbose=1
)

train_time = time.time() - start_time
print(f'\n✅ Training complete in {train_time:.2f}s')

🔧 Training Autoencoder on legitimate transactions...
Epoch 1/50
223/223 ━━━━━━━━━━━━━━━━━━━━ 19s 73ms/step - loss: 595.2077 - val_loss: 212.4183
Epoch 2/50
223/223 ━━━━━━━━━━━━━━━━━━━━ 16s 70ms/step - loss: 98.8201 - val_loss: 118.0123
Epoch 3/50
223/223 ━━━━━━━━━━━━━━━━━━━━ 14s 65ms/step - loss: 45.5730 - val_loss: 39.0268
Epoch 4/50
223/223 ━━━━━━━━━━━━━━━━━━━━ 17s 77ms/step - loss: 30.6756 - val_loss: 25.3966
Epoch 5/50
223/223 ━━━━━━━━━━━━━━━━━━━━ 17s 76ms/step - loss: 22.9655 - val_loss: 14.1279
Epoch 6/50
223/223 ━━━━━━━━━━━━━━━━━━━━ 17s 76ms/step - loss: 21.3364 - val_loss: 15.9253
Epoch 7/50
223/223 ━━━━━━━━━━━━━━━━━━━━ 15s 69ms/step - loss: 19.3559 - val_loss: 14.3358
Epoch 8/50
223/223 ━━━━━━━━━━━━━━━━━━━━ 15s 68ms/step - loss: 19.8353 - val_loss: 31.5299
Epoch 9/50
223/223 ━━━━━━━━━━━━━━━━━━━━ 15s 66ms/step - loss: 15.2891 - val_loss: 16.4355
Epoch 10/50
223/223 ━━━━━━━━━━━━━━━━━━━━ 15s 67ms/step - loss: 15.4782 - val_loss: 8.9482
Epoch 11/50
223/223 ━━━━━━━━━━━━━━━━━━━━ 14s

In [33]:
def get_reconstruction_error(model, X):
    """Calculate MSE reconstruction error"""
    X_pred = model.predict(X, verbose=0)
    mse = np.mean(np.power(X - X_pred, 2), axis=1)
    return mse

train_errors = get_reconstruction_error(autoencoder, X_train)
val_errors = get_reconstruction_error(autoencoder, X_val)

print(f'📊 Train reconstruction error stats:')
print(f'  Mean: {train_errors.mean():.6f}')
print(f'  Std: {train_errors.std():.6f}')
print(f'  Min: {train_errors.min():.6f}')
print(f'  Max: {train_errors.max():.6f}')

📊 Train reconstruction error stats:
  Mean: 4.034517
  Std: 18.997992
  Min: 0.025946
  Max: 1530.341819


In [34]:
fig = make_subplots(rows=1, cols=2, subplot_titles=('Error Distribution by Class', 'Error Box Plot'))

fig.add_trace(
    go.Histogram(x=val_errors[y_val == 0], name='Legitimate',
                 marker_color=COLORS['secondary'], opacity=0.7, nbinsx=50),
    row=1, col=1
)
fig.add_trace(
    go.Histogram(x=val_errors[y_val == 1], name='Fraud',
                 marker_color=COLORS['danger'], opacity=0.7, nbinsx=50),
    row=1, col=1
)

fig.add_trace(
    go.Box(y=val_errors[y_val == 0], name='Legitimate', marker_color=COLORS['secondary']),
    row=1, col=2
)
fig.add_trace(
    go.Box(y=val_errors[y_val == 1], name='Fraud', marker_color=COLORS['danger']),
    row=1, col=2
)

fig.update_layout(
    title='📊 Autoencoder Reconstruction Error Analysis',
    title_font_size=18,
    height=400
)

fig.update_xaxes(title_text='Reconstruction Error', row=1, col=1)
fig.update_yaxes(title_text='Count', row=1, col=1)

fig.show()
fig.write_html(f'{BASE_PATH}/reports/figures/26_autoencoder_errors.html')

In [35]:
from sklearn.metrics import precision_recall_curve

precision, recall, thresholds = precision_recall_curve(y_val, val_errors)
f1_scores = 2 * (precision * recall) / (precision + recall + 1e-8)

best_idx = np.argmax(f1_scores)
best_threshold = thresholds[best_idx] if best_idx < len(thresholds) else thresholds[-1]

print(f'📊 Optimal threshold: {best_threshold:.6f}')
print(f'📊 Best F1 score: {f1_scores[best_idx]:.4f}')

📊 Optimal threshold: 9.835533
📊 Best F1 score: 0.2500


In [36]:
ae_pred = (val_errors > best_threshold).astype(int)
ae_proba = (val_errors - val_errors.min()) / (val_errors.max() - val_errors.min())

ae_metrics = {
    'model': 'Autoencoder (Anomaly)',
    'accuracy': accuracy_score(y_val, ae_pred),
    'precision': precision_score(y_val, ae_pred),
    'recall': recall_score(y_val, ae_pred),
    'f1': f1_score(y_val, ae_pred),
    'roc_auc': roc_auc_score(y_val, val_errors),
    'pr_auc': average_precision_score(y_val, val_errors),
    'train_time': train_time
}

all_results.append(ae_metrics)
trained_models['autoencoder'] = autoencoder

print('📊 Validation Results:')
for k, v in ae_metrics.items():
    if k != 'model':
        print(f'  {k}: {v:.4f}' if isinstance(v, float) else f'  {k}: {v}')

📊 Validation Results:
  accuracy: 0.9159
  precision: 0.1815
  recall: 0.4001
  f1: 0.2497
  roc_auc: 0.7840
  pr_auc: 0.1578
  train_time: 690.9214


## 6️⃣ Model Comparison

In [37]:
results_df = pd.DataFrame(all_results)
results_df = results_df.sort_values('roc_auc', ascending=False)

print('📊 Deep Learning Model Comparison (Sorted by ROC-AUC):')
results_df

📊 Deep Learning Model Comparison (Sorted by ROC-AUC):


model  accuracy  precision    recall        f1   roc_auc  \
0              Basic MLP  0.845684   0.153043  0.751814  0.254316  0.883051   
1   Deep NN (Focal Loss)  0.970773   0.901176  0.185293  0.307384  0.868575   
2  Autoencoder (Anomaly)  0.915857   0.181519  0.400097  0.249736  0.784032   

     pr_auc   train_time  
0  0.469046   796.804916  
1  0.459582  2289.842023  
2  0.157775   690.921427

In [38]:
fig = make_subplots(
    rows=2, cols=2,
    subplot_titles=('ROC-AUC Score', 'PR-AUC Score', 'F1 Score', 'Training Time (s)')
)

colors = [COLORS['primary'], COLORS['secondary'], COLORS['warning']]

metrics_to_plot = ['roc_auc', 'pr_auc', 'f1', 'train_time']
positions = [(1, 1), (1, 2), (2, 1), (2, 2)]

for metric, pos in zip(metrics_to_plot, positions):
    fig.add_trace(
        go.Bar(
            x=results_df['model'],
            y=results_df[metric],
            marker_color=colors[:len(results_df)],
            text=[f'{x:.4f}' if metric != 'train_time' else f'{x:.1f}s' for x in results_df[metric]],
            textposition='outside'
        ),
        row=pos[0], col=pos[1]
    )

fig.update_layout(
    title='📊 Deep Learning Models Comparison',
    title_font_size=20,
    height=600,
    showlegend=False
)

fig.update_xaxes(tickangle=45)

fig.show()
fig.write_html(f'{BASE_PATH}/reports/figures/27_dl_model_comparison.html')

In [39]:
fig = go.Figure()

models_probas = {
    'Basic MLP': mlp_proba,
    'Deep NN (Focal Loss)': dnn_proba,
    'Autoencoder': ae_proba
}

for idx, (name, proba) in enumerate(models_probas.items()):
    if name == 'Autoencoder':
        fpr, tpr, _ = roc_curve(y_val, val_errors)
        auc = roc_auc_score(y_val, val_errors)
    else:
        fpr, tpr, _ = roc_curve(y_val, proba)
        auc = roc_auc_score(y_val, proba)
    
    fig.add_trace(
        go.Scatter(
            x=fpr, y=tpr,
            mode='lines',
            name=f'{name} (AUC={auc:.4f})',
            line=dict(width=2)
        )
    )

fig.add_trace(
    go.Scatter(x=[0, 1], y=[0, 1], mode='lines',
               line=dict(dash='dash', color='gray'), showlegend=False)
)

fig.update_layout(
    title='📈 Deep Learning ROC Curves Comparison',
    title_font_size=18,
    xaxis_title='False Positive Rate',
    yaxis_title='True Positive Rate',
    height=500,
    legend=dict(x=0.6, y=0.1)
)

fig.show()
fig.write_html(f'{BASE_PATH}/reports/figures/28_dl_roc_comparison.html')

## 7️⃣ Save Models & Results

In [40]:
print('💾 Saving models...')

mlp_model.save(f'{BASE_PATH}/models/dl/mlp_final.keras')
deep_nn.save(f'{BASE_PATH}/models/dl/deep_nn_final.keras')
autoencoder.save(f'{BASE_PATH}/models/dl/autoencoder_final.keras')
encoder.save(f'{BASE_PATH}/models/dl/encoder_final.keras')

print('✅ All DL models saved!')

💾 Saving models...
✅ All DL models saved!


In [41]:
results_df.to_csv(f'{BASE_PATH}/reports/metrics/dl_model_results.csv', index=False)

best_dl_model = results_df.iloc[0]['model']
best_dl_info = {
    'best_dl_model': best_dl_model,
    'roc_auc': float(results_df.iloc[0]['roc_auc']),
    'pr_auc': float(results_df.iloc[0]['pr_auc']),
    'f1': float(results_df.iloc[0]['f1'])
}

with open(f'{BASE_PATH}/reports/metrics/best_dl_model.json', 'w') as f:
    json.dump(best_dl_info, f, indent=2)

ae_config = {
    'optimal_threshold': float(best_threshold),
    'error_mean': float(train_errors.mean()),
    'error_std': float(train_errors.std())
}

with open(f'{BASE_PATH}/models/dl/autoencoder_config.json', 'w') as f:
    json.dump(ae_config, f, indent=2)

print(f'\n🏆 Best DL Model: {best_dl_model}')
print(f'   ROC-AUC: {best_dl_info["roc_auc"]:.4f}')


🏆 Best DL Model: Basic MLP
   ROC-AUC: 0.8831
